<p float="left">
  <img src="PlantHub-full-rgb.png" style="height:100px" alt="PlantHub logo" class="light-logo">
  <img src="PlantHub-full-white.png" style="height:100px" alt="PlantHub logo" class="dark-logo">
  <img src="gfoe.png" style="height:100px" alt="gfö logo" class="light-logo">
  <img src="gfoe_inv.png" style="height:100px" alt="gfö logo" class="dark-logo">
  <img src="NFDI4Biodiversity.svg" style="height:100px" alt="NFDI logo" class="light-logo">
   <img src="NFDI4Biodiversity_text_inv.svg" style="height:100px" alt="NFDI 2023 logo" class="dark-logo">
</p>

# Taxonomic name parsing

This notebook is intended to show the functionality of a taxonomic name parser. Name parsing describes the identification of string components as parts of scientific names. In general, these are 
- generic name/genus,
- specific name/epithet,
- infraspecies markers (subsp./var./f.),
- infraspecific name/epithet,
- authors.

 Additional elements, as hybrid signs and a number of other markers as cv. or agg., spelling errors, and custom information in the names, e.g., <i>Bellis perennis</i>_plot123, can complicate the process of name parsing.
 In this notebook, the taxonomic name parser from [GBIF](https://www.gbif.org/tools/name-parser) will be used. However, there are some limitation with it, and in the hands-on part, we will attempt to overcome those by pre-processing the data before sending it to the name parser. We will also try to speed up the name parsing process by using the parallel processing functionality of R.

## Prerequisites

To run the code presented here, you will need 
- the sample names list provided in the workshop,
- a functioning R environment and 
- the R packages `data.table`, `rgbif`, and `doSNOW` installed.

## Code

The first block of code loads libraries and prepares the workspace. You will need to adapt the working directory.

In [1]:
# load packages
library(data.table) # handle large datasets
library(rgbif) # access GBIF data
library(doSNOW) # parallel computing

# clear workspace
rm(list = ls())

# set working directory
setwd(paste0(.brd, "gfoe NFDI taxonomic harmonization workshop"))

# load data
plants <- fread("plant names_2024-04-08.txt", sep = "\t")
animals <- fread("animal names_2024-04-09.txt", sep = "\t")


Lade nötiges Paket: foreach

Lade nötiges Paket: iterators

Lade nötiges Paket: snow



Both the plants and animals variables are tables with one column. The names in these tables are different from each other - most notably, some have authors included while others have not. To get the best results when doing name harmonization later on, we will need to separate authors, and also remove problematic characters from the data.

### Encoding

Unfortunately, when getting data from differing sources, we will often find that these data have been [encoded](https://en.wikipedia.org/wiki/Binary-to-text_encoding) in different ways. This means that while the typical English language letters will be stored the same way on any machine, when it comes to accents and some other special characters, it may matter whether data was stored by a computer in the US or Japan, and whether the computer has a Windows, Mac, or Linux operating system. 

We will deal with the most common case: Data being stored in the Windows-specific [CP-1252 encoding](https://en.wikipedia.org/wiki/Windows-1252) (mislabeled ANSI or latin1 sometimes) and not in [UTF-8](https://en.wikipedia.org/wiki/UTF-8).

How your machine treats data from different encodings depends on what encoding is preset in your console. You can check this using the following:

In [2]:
Sys.getlocale()


[1] "LC_COLLATE=German_Germany.utf8;LC_CTYPE=German_Germany.utf8;LC_MONETARY=German_Germany.utf8;LC_NUMERIC=C;LC_TIME=German_Germany.utf8"

If your console has no UTF-8 setting (no matter the language) you may change it like this: 

`Sys.setlocale(category = "LC_ALL", locale = "German_Germany.utf8")`

You can use another encoding, too, but it may throw errors later on. So let's check whether the data comes in UTF-8, and if not, let's repair it, assuming it is CP-1252 (our best guess, likely correct in 99% of the cases).

In [3]:
# check whether correct encoding is UTF-8
table(validUTF8(plants$oldName))
table(validUTF8(animals$modName))



FALSE  TRUE 
   73  4927 


TRUE 
5000 

In [4]:
# create new columns for variables
plants[, newName := oldName]
animals[, newName := modName]
# correct encoding, assuming current encoding is CP-1252
plants[!validUTF8(newName), newName := iconv(newName, from = "CP1252", to = "UTF-8")]


### Name parsing

Let's try to parse the names using the GBIF name parser.

In [5]:
resP <- data.table(name_parse(plants$newName))
resA <- data.table(name_parse(animals$newName))

table(resP$parsed)
table(resA$parsed)



FALSE  TRUE 
   11  4989 


FALSE  TRUE 
   17  4983 

That looks like a pretty good result. For plants and animals, we got all but 11 and 12 names parsed, respectively.
Let's look at what did not work for animals.

In [6]:
resA[parsed == FALSE]


scientificname                                                 type   
1  W0_758_Allobates hodli Simões, Lima & Farias                   NO_NAME
2  Andinobates spec X Batista, Jaramillo, Ponce, & Crawford, 2014 HYBRID 
3  XM3_777_Anthracothorax viridis (Audebert & Vieillot, 1801)     NO_NAME
4  U_291_Balearica pavonina (Linnaeus, 1758)                      NO_NAME
5  Q4_650_Colpophyllia Milne Edwards & Haime                      NO_NAME
6  O_824_Crypthelia glebulenta Cairns, 1986                       NO_NAME
7  DISsOSURA LONGICAUDUS (Gmelin, 1788)                           NO_NAME
8  C9_428_Euphlyctis hexadactylus (Lesson, 1834)                  NO_NAME
9  0S_65_Flabellum siboae Gardiner, 1904                          NO_NAME
10 165_251_Glaucidium nubicola Robbins & Stiles, 1999             NO_NAME
11 HOMOPUq AREOLATUS (Thunberg, 1787)                             NO_NAME
12 LEPIDOPhRA SYMMETRICA Cairns, 1991                             NO_NAME
13 P_944_Podocnemis erythrocephala (Spix, 1824)                   NO_NAME
14 X_242_RHODOPIS                                                 NO_NAME
15 0P_663_Saiga tatarica (Linnaeus, 1766)                         NO_NAME
16 98Y_336_Stichopathes semiglabra (van Pesch, 1914)              NO_NAME
17 6X_832_Uroplatus henkeli                                       NO_NAME
   genusorabove authorship year parsed parsedpartially canonicalname
1  NA           NA         NA   FALSE  FALSE           NA           
2  NA           NA         NA   FALSE  FALSE           NA           
3  NA           NA         NA   FALSE  FALSE           NA           
4  NA           NA         NA   FALSE  FALSE           NA           
5  NA           NA         NA   FALSE  FALSE           NA           
6  NA           NA         NA   FALSE  FALSE           NA           
7  NA           NA         NA   FALSE  FALSE           NA           
8  NA           NA         NA   FALSE  FALSE           NA           
9  NA           NA         NA   FALSE  FALSE           NA           
10 NA           NA         NA   FALSE  FALSE           NA           
11 NA           NA         NA   FALSE  FALSE           NA           
12 NA           NA         NA   FALSE  FALSE           NA           
13 NA           NA         NA   FALSE  FALSE           NA           
14 NA           NA         NA   FALSE  FALSE           NA           
15 NA           NA         NA   FALSE  FALSE           NA           
16 NA           NA         NA   FALSE  FALSE           NA           
17 NA           NA         NA   FALSE  FALSE           NA           
   canonicalnamecomplete canonicalnamewithmarker specificepithet
1  NA                    NA                      NA             
2  NA                    NA                      NA             
3  NA                    NA                      NA             
4  NA                    NA                      NA             
5  NA                    NA                      NA             
6  NA                    NA                      NA             
7  NA                    NA                      NA             
8  NA                    NA                      NA             
9  NA                    NA                      NA             
10 NA                    NA                      NA             
11 NA                    NA                      NA             
12 NA                    NA                      NA             
13 NA                    NA                      NA             
14 NA                    NA                      NA             
15 NA                    NA                      NA             
16 NA                    NA                      NA             
17 NA                    NA                      NA             
   bracketauthorship bracketyear rankmarker infraspecificepithet infrageneric
1  NA                NA          NA         NA                   NA          
2  NA                NA          NA         NA                   NA          
3  NA                NA  

### Pre-processing

The problem with most of these names is the number-character combinations before the actual name. They need to be removed before using the name parser. As it seems these are combinations of one to three uppercase characters or numbers followed by a underline repeated twice, we may find them like shown below. Note that is essential to use [regular expressions](https://en.wikipedia.org/wiki/Regular_expression), which can be used to create target patterns to search for. Regular expressions are more or less the same across programming languages. Some information specifically on R can be found [here](https://www.rdocumentation.org/packages/base/versions/3.6.2/topics/regex).

In [7]:
animals[grepl("^([[:upper:]]|\\d){1,3}_([[:upper:]]|\\d){1,3}", newName), "newName"]


newName                                                   
1  W0_758_Allobates hodli Simões, Lima & Farias              
2  XM3_777_Anthracothorax viridis (Audebert & Vieillot, 1801)
3  U_291_Balearica pavonina (Linnaeus, 1758)                 
4  WCO_501_Calliphlox mitchellii (Bourcier, 1847)            
5  Q4_650_Colpophyllia Milne Edwards & Haime                 
6  O_824_Crypthelia glebulenta Cairns, 1986                  
7  C9_428_Euphlyctis hexadactylus (Lesson, 1834)             
8  0S_65_Flabellum siboae Gardiner, 1904                     
9  165_251_Glaucidium nubicola Robbins & Stiles, 1999        
10 P_944_Podocnemis erythrocephala (Spix, 1824)              
11 X_242_RHODOPIS                                            
12 0P_663_Saiga tatarica (Linnaeus, 1766)                    
13 98Y_336_Stichopathes semiglabra (van Pesch, 1914)         
14 6X_832_Uroplatus henkeli

Removing such a sequence could be done more or less like this.

In [8]:
# create a new variable to not overwrite the original data
animals[, testName := newName]

# remove the name sequences
animals[, testName := sub("^([[:upper:]]|\\d){1,3}_([[:upper:]]|\\d){1,3}", "", testName)]

# check whether it worked
animals[testName != newName, c("newName", "testName")]


newName                                                   
1  W0_758_Allobates hodli Simões, Lima & Farias              
2  XM3_777_Anthracothorax viridis (Audebert & Vieillot, 1801)
3  U_291_Balearica pavonina (Linnaeus, 1758)                 
4  WCO_501_Calliphlox mitchellii (Bourcier, 1847)            
5  Q4_650_Colpophyllia Milne Edwards & Haime                 
6  O_824_Crypthelia glebulenta Cairns, 1986                  
7  C9_428_Euphlyctis hexadactylus (Lesson, 1834)             
8  0S_65_Flabellum siboae Gardiner, 1904                     
9  165_251_Glaucidium nubicola Robbins & Stiles, 1999        
10 P_944_Podocnemis erythrocephala (Spix, 1824)              
11 X_242_RHODOPIS                                            
12 0P_663_Saiga tatarica (Linnaeus, 1766)                    
13 98Y_336_Stichopathes semiglabra (van Pesch, 1914)         
14 6X_832_Uroplatus henkeli                                  
   testName                                           
1  _Allobates hodli Simões, Lima & Farias             
2  _Anthracothorax viridis (Audebert & Vieillot, 1801)
3  _Balearica pavonina (Linnaeus, 1758)               
4  _Calliphlox mitchellii (Bourcier, 1847)            
5  _Colpophyllia Milne Edwards & Haime                
6  _Crypthelia glebulenta Cairns, 1986                
7  _Euphlyctis hexadactylus (Lesson, 1834)            
8  _Flabellum siboae Gardiner, 1904                   
9  _Glaucidium nubicola Robbins & Stiles, 1999        
10 _Podocnemis erythrocephala (Spix, 1824)            
11 _RHODOPIS                                          
12 _Saiga tatarica (Linnaeus, 1766)                   
13 _Stichopathes semiglabra (van Pesch, 1914)         
14 _Uroplatus henkeli

>TASKS:
>1) Try to fix the code so that it gives the wanted result. 
>2) To increase the accuracy of later matching, look for these combinations of uppercase letters and numbers also in the species epithet. 
>3) Then, try to fix the problems with the other unparsed names in the animal and plant names.
>4) There may also be some generic terms you may want to remove (e.g. spec., spp., agg., etc.).
>
> Some useful functions can be found below.


In [9]:
# check for a number after the genus name, but before the year
animals[grepl("^\\S+\\s.*\\d.*\\s\\d{4}$", newName), "newName"][1:3]
resA[grepl("^\\S+\\s.*\\d.*\\s\\d{4}$", animals$newName)][1:3]

# check for spec., species, morpho, spp.
animals[grepl("spec\\.|species|morpho|spp\\.", newName), "newName"][1:3]
resA[grepl("spec\\.|species|morpho|spp\\.", animals$newName)][1:3]

# find name parts after an equal sign
plants[grepl("=", newName), "newName"][1:3]
resP[grepl("=", plants$newName)][1:3]


newName                                             
1 ACANTHASTREA LORDHOWENSIS_4_889 Veron & Pichon, 1982
2 Accipiter spp.-5 Rothschild & Hartert, 1926         
3 Acropora morphospec1 Veron & Wallace, 1984

scientificname                                       type       genusorabove
1 ACANTHASTREA LORDHOWENSIS_4_889 Veron & Pichon, 1982 DOUBTFUL   Acanthastrea
2 Accipiter spp.-5 Rothschild & Hartert, 1926          INFORMAL   Accipiter   
3 Acropora morphospec1 Veron & Wallace, 1984           SCIENTIFIC Acropora    
  authorship   year parsed parsedpartially canonicalname  
1 Lordhowensis NA   TRUE   TRUE            Acanthastrea   
2 NA           NA   TRUE   TRUE            Accipiter spec.
3 NA           NA   TRUE   TRUE            Acropora       
  canonicalnamecomplete     canonicalnamewithmarker specificepithet
1 Acanthastrea Lordhowensis Acanthastrea            NA             
2 Accipiter spec.           Accipiter spec.         NA             
3 Acropora                  Acropora                NA             
  bracketauthorship bracketyear rankmarker infraspecificepithet infrageneric
1 NA                NA          NA         NA                   NA          
2 NA                NA          sp.        NA                   NA          
3 NA                NA          NA         NA                   NA          
  cultivarepithet sensu
1 NA              NA   
2 NA              NA   
3 NA              NA

newName                                    
1 Accipiter spp.-5 Rothschild & Hartert, 1926
2 Acropora morphospec1 Veron & Wallace, 1984 
3 Brookesia spp. Q Brygoo & Domergue, 1975

scientificname                              type       genusorabove
1 Accipiter spp.-5 Rothschild & Hartert, 1926 INFORMAL   Accipiter   
2 Acropora morphospec1 Veron & Wallace, 1984  SCIENTIFIC Acropora    
3 Brookesia spp. Q Brygoo & Domergue, 1975    INFORMAL   Brookesia   
  authorship year parsed parsedpartially canonicalname   canonicalnamecomplete
1 NA         NA   TRUE    TRUE           Accipiter spec. Accipiter spec.      
2 NA         NA   TRUE    TRUE           Acropora        Acropora             
3 NA         NA   TRUE   FALSE           Brookesia spp.Q Brookesia spp.Q      
  canonicalnamewithmarker specificepithet bracketauthorship bracketyear
1 Accipiter spec.         NA              NA                NA         
2 Acropora                NA              NA                NA         
3 Brookesia spp.Q         spp.Q           NA                NA         
  rankmarker infraspecificepithet infrageneric cultivarepithet sensu
1 sp.        NA                   NA           NA              NA   
2 NA         NA                   NA           NA              NA   
3 sp.        NA                   NA           NA              NA

newName                                                             
1 Artemisia vulgaris x verlotiorum = A. x wurzellii C.M. James & Stace
2 Lolium perenne x multiflorum = L. x boucheanum Kunth                
3 Mentha arvensis x aquatica x spicata = M. x smithiana R.A. Graham

scientificname                                                       type  
1 Artemisia vulgaris x verlotiorum = A. x wurzellii C.M. James & Stace HYBRID
2 Lolium perenne x multiflorum = L. x boucheanum Kunth                 HYBRID
3 Mentha arvensis x aquatica x spicata = M. x smithiana R.A. Graham    HYBRID
  parsed parsedpartially genusorabove canonicalname canonicalnamecomplete
1 FALSE  FALSE           NA           NA            NA                   
2 FALSE  FALSE           NA           NA            NA                   
3 FALSE  FALSE           NA           NA            NA                   
  canonicalnamewithmarker rankmarker specificepithet authorship
1 NA                      NA         NA              NA        
2 NA                      NA         NA              NA        
3 NA                      NA         NA              NA        
  infraspecificepithet bracketauthorship notho sensu nomstatus strain
1 NA                   NA                NA    NA    NA        NA    
2 NA                   NA                NA    NA    NA        NA    
3 NA                   NA                NA    NA    NA        NA

You can compare your results to the ones provided here below. For plants, they have been created using a name parser developed specifically for the names of the TRY database. For animals this is an extract of the [CITES names list](https://checklist.cites.org/#/en), these are the unmodified correct names, from which the erronous names found here were derived.


In [10]:
# for testing
plantsFull <- fread("plant names full_2024-04-08.txt", sep = ",")
animalsFull <- fread("animal names full_2024-04-09.txt", sep = ",")


In [11]:
str(plantsFull)
str(animalsFull)


Classes 'data.table' and 'data.frame':	5000 obs. of  18 variables:
 $ oldName         : chr  "" "(lauraceae) pubescente" "?Betulaceae sp." "Abarema curvicarpa" ...
 $ newName         : chr  "" "" "" "" ...
 $ familyNameFound : logi  FALSE TRUE TRUE FALSE FALSE FALSE ...
 $ oldFamilyName   : chr  "" "lauraceae" "Betulaceae" "" ...
 $ newFamilyName   : chr  "" "Lauraceae" "Betulaceae" "" ...
 $ genus           : chr  "" "Pubescente" "" "Abarema" ...
 $ hybrid1         : chr  "" "" "" "" ...
 $ species1        : chr  "" "" "" "curvicarpa" ...
 $ subSpeciesFlag  : chr  "" "" "" "" ...
 $ subSpecies      : chr  "" "" "" "" ...
 $ varSpeciesFlag  : chr  "" "" "" "" ...
 $ varSpecies      : chr  "" "" "" "" ...
 $ formaSpeciesFlag: logi  NA NA NA NA NA NA ...
 $ formaSpecies    : logi  NA NA NA NA NA NA ...
 $ hybrid2         : chr  "" "" "" "" ...
 $ species2        : chr  "" "" "" "" ...
 $ author          : chr  "" "" "" "" ...
 $ kingdom         : chr  "" "" "" "P" ...
 - attr(*, ".intern

### Parallel processing

With our name lists having 5000 names each, the parsing takes just some seconds. Depending on the size of the list, it may be a good idea to speed up the process by parallelizing it. As the `name_parse` function already accepts several names at once, we may split the names list into the number of cores we can use for parallel processing.

Let's check how many cores are available on the system.

In [12]:
parallel::detectCores()


[1] 16

It is unlikely that you have so many cores available, but from former trials with the GBIF API I can tell you that is is wise to limit the core number to 24 at maximum. So let's re-run the name parsing to compare the times needed. 

In [13]:
timeStart <- Sys.time()
resP <- data.table(name_parse(plants$newName))
Sys.time() - timeStart
timeStart <- Sys.time()
resA <- data.table(name_parse(animals$newName))
Sys.time() - timeStart


Time difference of 1.98634 secs

Time difference of 3.512737 secs

Now let's split the lists into chunks and let each worker run independently.

In [14]:
nLists <- min(24, parallel::detectCores() - 1)
(nNames <- nrow(plants) %/% nLists)
(nNamesLast <- nNames + nrow(plants) %% nLists)


[1] 333

[1] 338

We chose to use one workers less than we can, to allow the computer to fulfill other tasks while the script is running, and a maximum of 24. On my computer, this means that each chunk has 333 names to process, and the last chunk will have 338. Let's create the parallel environment now and compare the times. We just to the plant case for simplicity.

In [15]:
# create the cluster for parallel processing
cl <- makeCluster(nLists)
registerDoSNOW(cl)

# run the name parsing in parallel
# the option "fill = TRUE" makes sure foreach throws no error due to different column numbers
timeStart <- Sys.time()
resP_parallel <- foreach(
	i = seq_len(nLists), .combine = function(...) rbind(..., fill = TRUE),
	.packages = c("data.table", "rgbif")
) %dopar% {
	if (i < nLists) {
		res <- data.table(name_parse(plants$newName[seq_len(nNames) + (i - 1) * nNames]))
	} else {
		res <- data.table(name_parse(plants$newName[seq_len(nNamesLast) + (i - 1) * nNames]))
	}
	res
}
Sys.time() - timeStart

# stop the cluster
stopCluster(cl)


Time difference of 5.201381 secs

Timewise, for this little dataset, the overhead created by setting up the parallel environment was larger than the speed gain through parallel processing. Let's check whether the results are the same.

In [16]:
all(resP == resP_parallel, na.rm = TRUE)


[1] TRUE

However, the results are as expected, and with larger lists, this approach could save us some time.